In [1]:
import torch
import random
import numpy as np
import os

import glob
import tifffile as tiff

import errno
import imageio

from PIL import Image
from torch.utils import data

from NNUtils import CustomDataset

import matplotlib.pyplot as plt

In [2]:
# read data set and pick up one picture
test_data = '/home/moucheng/projects_data/Brain_data/brats2018/t5_s20_l1_u30_WT/test'
test_data_images = test_data + '/patches'
test_data_labels = test_data + '/labels'
dataset = CustomDataset(test_data_images, test_data_labels, 'none', 3)
dataloader = data.DataLoader(dataset, batch_size=1, shuffle=False, num_workers=1, drop_last=False)

In [3]:
# # check data
# index = 10
# images1, images2, images3, labels, imagename = dataset[index]

# plt.imshow(np.squeeze(images2), cmap='gray')
# plt.title('Input')
# plt.show()

# plt.imshow(np.squeeze(labels), cmap='gray')
# plt.title('Labels')
# plt.show()

# overlay = 0.6*np.squeeze(images2) + 0.4*np.squeeze(labels)
# plt.imshow(np.squeeze(overlay), cmap='gray')
# plt.title('Overlay')
# plt.show()

In [4]:
def test_inference(dataset, model, model_name, device):
    
    for index in range(len(dataset)):

        images1, images2, images3, labels, imagename = dataset[index]

        images1 = torch.from_numpy(images1).float()
        images2 = torch.from_numpy(images2).float()
        images3 = torch.from_numpy(images3).float()
        labels = torch.from_numpy(labels).float()

        test_img1 = images1.to(device=device, dtype=torch.float32)
        test_img2 = images2.to(device=device, dtype=torch.float32)
        test_img3 = images3.to(device=device, dtype=torch.float32)
        test_labels = labels.to(device=device, dtype=torch.float32)

        c, h, w = test_img1.size()
            
        test_img1 = test_img1.view(1, c, h, w)
        test_img2 = test_img2.view(1, c, h, w)
        test_img3 = test_img3.view(1, c, h, w)
        
        if 'ERFAnetZ' in model_name:
        
            # For ours:
            test_outputs_fp, test_outputs_fn, test_pseudo_x1_a, test_pseudo_x1_b, test_pseudo_x2, test_pseudo_x3_a, test_pseudo_x3_b, test_x_, test_x__, test_x___ = model(test_img1, test_img2, test_img3)
            test_outputs_fp = torch.sigmoid(test_outputs_fp)
            test_outputs_fn = torch.sigmoid(test_outputs_fn)
            test_class_outputs = (test_outputs_fn + test_outputs_fp) / 2

        elif 'MTASSUnet' in model_name:
            # For mtass:
            test_outputs, _ = model(test_img2)
            test_class_outputs = torch.sigmoid(test_outputs)
            
        elif 'FixMatch' in model_name or 'MeanTeacher' in model_name or 'Unet' in model_name:
            # For fixmatch, meanTeacher, Unet:
            test_outputs = model(test_img2)
            test_class_outputs = torch.sigmoid(test_outputs)
        
        save_path = '/home/moucheng/projects_data/Brain_data/results'
        save_path = save_path + '/' + model_name

        try:

            os.mkdir(save_path)

        except OSError as exc:

            if exc.errno != errno.EEXIST:

                raise

            pass

        b, c, h, w = test_img2.size()

        pred = test_class_outputs.reshape(h, w).cpu().detach().numpy() > 0.5
        pred = np.asarray(pred, dtype=np.uint8)
        
        if c == 1:
            testimg = test_img2.cpu().squeeze().detach().numpy()
            testimg = np.asarray(testimg, dtype=np.float32)
        else:
            testimg = test_img2.cpu().squeeze().detach().numpy()
            testimg = testimg[2, :, :]
            testimg = np.asarray(testimg, dtype=np.float32)

        label = test_labels.squeeze().cpu().detach().numpy() > 0.5
        label = np.asarray(label, dtype=np.uint8)

        difference = label - pred
        addition = label + pred

        error_map = np.zeros((h, w, 3), dtype=np.uint8)
        label_map = np.zeros((h, w, 3), dtype=np.uint8)

        error_map[difference == -1] = [255, 0, 0]  # false positive red
        error_map[difference == 1] = [0, 0, 255]  # false negative blue
        error_map[addition == 2] = [0, 255, 0]  # true positive green

        label_map[label == 1] = [255, 255, 0]  # true positive yellow

        prediction_name = 'seg_' + imagename + '.png'
        full_error_map_name = os.path.join(save_path, prediction_name)
        imageio.imsave(full_error_map_name, error_map)

        pic_name = 'original_' + imagename + '.png'
        full_pic_map_name = os.path.join(save_path, pic_name)
        imageio.imsave(full_pic_map_name, testimg)

        label_name = 'label_' + imagename + '.png'
        full_label_map_name = os.path.join(save_path, label_name)
        imageio.imsave(full_label_map_name, label_map)

        seg_img = Image.open(full_error_map_name)
        input_img = Image.open(full_pic_map_name)
        label_img = Image.open(full_label_map_name)

        seg_img = seg_img.convert("RGBA")
        input_img = input_img.convert("RGBA")
        label_img = label_img.convert("RGBA")

        alphaBlended_seg = Image.blend(seg_img, input_img, alpha=.6)
        alphaBlended_label = Image.blend(label_img, input_img, alpha=.6)

        imageio.imsave(full_error_map_name, alphaBlended_seg)
        imageio.imsave(full_label_map_name, alphaBlended_label)

In [5]:
# model_name = 'Unet_labelled_repeat_1_augmentation_all_lr_2e-05_epoch_50_CARVE2014_4_r176_s50_epoch40'
# model_path = '/home/moucheng/Desktop/IPMI results/CARVE2014/4_r176_s50/IPMI2020/Unet_labelled_repeat_1_augmentation_all_lr_2e-05_epoch_50_CARVE2014_4_r176_s50/trained_models'

# model = model_name + '.pt'
# model = model_path + '/' + model

# model = torch.load(model)
# model.eval()

# device = torch.device('cuda')

def test_models(model_name_list, model_path, dataset):
    
    for model_name in model_name_list:
        
        model = model_name + '.pt'
        model = model_path + '/' + model

        model = torch.load(model)
        model.eval()
        
        device = torch.device('cuda')
        
        test_inference(dataset, model, model_name, device)

In [20]:
model_name_list = ['Unet_labelled_repeat_1_augmentation_all_lr_2e-06_epoch_80_BRATS2018_t5_s20_l1_u30_WT_Final']

model_path = '/home/moucheng/Desktop/IPMI results/BRATS/IPMI2020/Unet_labelled_repeat_1_augmentation_all_lr_2e-06_epoch_80_BRATS2018_t5_s20_l1_u30_WT/trained_models'

test_models(model_name_list, model_path, dataset)

Lossy conversion from float32 to uint8. Range [-2.8014118671417236, 3.7762413024902344]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.8014118671417236, 3.754912853240967]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.8014118671417236, 3.9084768295288086]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.8014118671417236, 3.4477851390838623]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.8014118671417236, 3.9340708255767822]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.8014118671417236, 3.6951937675476074]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.8014118671417236, 4.1004319

Lossy conversion from float32 to uint8. Range [-2.8014118671417236, 4.535529613494873]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.8014118671417236, 4.748812675476074]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.8014118671417236, 5.077268600463867]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.8014118671417236, 4.9663615226745605]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.8014118671417236, 4.56965446472168]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.8014118671417236, 5.269223690032959]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.8014118671417236, 6.058371067047

Lossy conversion from float32 to uint8. Range [-2.306645393371582, 3.1989805698394775]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.306645393371582, 4.01984977722168]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.306645393371582, 3.3813960552215576]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.306645393371582, 3.961808443069458]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.306645393371582, 4.243722915649414]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.306645393371582, 4.334930419921875]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.306645393371582, 4.351513862609863]. 

Lossy conversion from float32 to uint8. Range [-2.4402499198913574, 7.396176338195801]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.4402499198913574, 7.016024589538574]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.4402499198913574, 7.36449670791626]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.4402499198913574, 8.291116714477539]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.4402499198913574, 7.728808879852295]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.4402499198913574, 6.493315696716309]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.4402499198913574, 6.3190793991088

Lossy conversion from float32 to uint8. Range [-3.8219411373138428, 11.646082878112793]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-3.8219411373138428, 11.792612075805664]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-3.8219411373138428, 12.351256370544434]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-3.8219411373138428, 12.506943702697754]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-3.8219411373138428, 11.691873550415039]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-3.8219411373138428, 11.728506088256836]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-3.8219411373138428, 11.94830

...

Lossy conversion from float32 to uint8. Range [-4.083411693572998, 6.305342674255371]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-4.083411693572998, 5.386525630950928]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-4.083411693572998, 6.4768548011779785]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-4.083411693572998, 7.922460079193115]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-4.083411693572998, 7.689692974090576]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-4.083411693572998, 8.387993812561035]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-4.083411693572998, 8.620760917663574]. 

Lossy conversion from float32 to uint8. Range [-4.083411693572998, 4.112433433532715]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-4.083411693572998, 5.055751800537109]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-4.083411693572998, 5.202762603759766]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-4.083411693572998, 4.651472568511963]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-4.083411693572998, 4.56571626663208]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-4.083411693572998, 4.247192859649658]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-4.083411693572998, 4.002175331115723]. Co

Lossy conversion from float32 to uint8. Range [-3.7180027961730957, 8.078850746154785]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-3.7180027961730957, 6.593591213226318]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-3.7180027961730957, 5.911832809448242]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-3.7180027961730957, 5.83878755569458]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-3.7180027961730957, 6.386629104614258]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-3.7180027961730957, 7.141432762145996]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-3.7180027961730957, 6.7153339385986

Lossy conversion from float32 to uint8. Range [-5.440743923187256, 5.01370096206665]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-5.440743923187256, 4.510490894317627]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-5.440743923187256, 4.243481636047363]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-5.440743923187256, 4.592647552490234]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-5.440743923187256, 4.654265403747559]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-5.440743923187256, 4.736422061920166]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-5.440743923187256, 4.808309078216553]. Co

Lossy conversion from float32 to uint8. Range [-5.440743923187256, 7.529751300811768]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-5.440743923187256, 7.714603900909424]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-5.440743923187256, 7.848108291625977]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-5.440743923187256, 7.878917217254639]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-5.440743923187256, 7.632447242736816]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-5.440743923187256, 7.673525333404541]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-5.440743923187256, 7.765951633453369]. C

In [15]:
model_name_list = ['MeanTeacher_repeat_3_alpha_0.002_lr_2e-06_epoch_80_annealing_down_at_0_beta_0.8_BRATS2018_t5_s20_l1_u30_WT_Final']

model_path = '/home/moucheng/Desktop/IPMI results/BRATS/IPMI2020/MeanTeacher_repeat_3_alpha_0.002_lr_2e-06_epoch_80_annealing_down_at_0_beta_0.8_BRATS2018_t5_s20_l1_u30_WT/trained_models'
test_models(model_name_list, model_path, dataset)

Lossy conversion from float32 to uint8. Range [-2.8014118671417236, 3.7762413024902344]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.8014118671417236, 3.754912853240967]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.8014118671417236, 3.9084768295288086]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.8014118671417236, 3.4477851390838623]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.8014118671417236, 3.9340708255767822]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.8014118671417236, 3.6951937675476074]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.8014118671417236, 4.1004319

Lossy conversion from float32 to uint8. Range [-2.8014118671417236, 4.535529613494873]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.8014118671417236, 4.748812675476074]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.8014118671417236, 5.077268600463867]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.8014118671417236, 4.9663615226745605]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.8014118671417236, 4.56965446472168]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.8014118671417236, 5.269223690032959]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.8014118671417236, 6.058371067047

Lossy conversion from float32 to uint8. Range [-2.306645393371582, 3.1989805698394775]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.306645393371582, 4.01984977722168]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.306645393371582, 3.3813960552215576]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.306645393371582, 3.961808443069458]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.306645393371582, 4.243722915649414]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.306645393371582, 4.334930419921875]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.306645393371582, 4.351513862609863]. 

Lossy conversion from float32 to uint8. Range [-2.4402499198913574, 7.396176338195801]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.4402499198913574, 7.016024589538574]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.4402499198913574, 7.36449670791626]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.4402499198913574, 8.291116714477539]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.4402499198913574, 7.728808879852295]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.4402499198913574, 6.493315696716309]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.4402499198913574, 6.3190793991088

Lossy conversion from float32 to uint8. Range [-3.8219411373138428, 11.646082878112793]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-3.8219411373138428, 11.792612075805664]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-3.8219411373138428, 12.351256370544434]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-3.8219411373138428, 12.506943702697754]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-3.8219411373138428, 11.691873550415039]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-3.8219411373138428, 11.728506088256836]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-3.8219411373138428, 11.94830

...

Lossy conversion from float32 to uint8. Range [-4.083411693572998, 6.305342674255371]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-4.083411693572998, 5.386525630950928]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-4.083411693572998, 6.4768548011779785]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-4.083411693572998, 7.922460079193115]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-4.083411693572998, 7.689692974090576]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-4.083411693572998, 8.387993812561035]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-4.083411693572998, 8.620760917663574]. 

Lossy conversion from float32 to uint8. Range [-4.083411693572998, 4.112433433532715]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-4.083411693572998, 5.055751800537109]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-4.083411693572998, 5.202762603759766]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-4.083411693572998, 4.651472568511963]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-4.083411693572998, 4.56571626663208]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-4.083411693572998, 4.247192859649658]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-4.083411693572998, 4.002175331115723]. Co

Lossy conversion from float32 to uint8. Range [-3.7180027961730957, 8.078850746154785]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-3.7180027961730957, 6.593591213226318]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-3.7180027961730957, 5.911832809448242]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-3.7180027961730957, 5.83878755569458]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-3.7180027961730957, 6.386629104614258]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-3.7180027961730957, 7.141432762145996]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-3.7180027961730957, 6.7153339385986

Lossy conversion from float32 to uint8. Range [-5.440743923187256, 5.01370096206665]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-5.440743923187256, 4.510490894317627]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-5.440743923187256, 4.243481636047363]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-5.440743923187256, 4.592647552490234]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-5.440743923187256, 4.654265403747559]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-5.440743923187256, 4.736422061920166]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-5.440743923187256, 4.808309078216553]. Co

Lossy conversion from float32 to uint8. Range [-5.440743923187256, 7.529751300811768]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-5.440743923187256, 7.714603900909424]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-5.440743923187256, 7.848108291625977]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-5.440743923187256, 7.878917217254639]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-5.440743923187256, 7.632447242736816]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-5.440743923187256, 7.673525333404541]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-5.440743923187256, 7.765951633453369]. C

In [16]:
model_name_list = ['FixMatch_repeat_1_alpha_0.002_lr_2e-06_epoch_40_annealing_down_at_0_beta_0.8_BRATS2018_t5_s20_l1_u30_WT_Final']

model_path = '/home/moucheng/Desktop/IPMI results/BRATS/IPMI2020/FixMatch_repeat_1_alpha_0.002_lr_2e-06_epoch_40_annealing_down_at_0_beta_0.8_BRATS2018_t5_s20_l1_u30_WT/trained_models'

test_models(model_name_list, model_path, dataset)

Lossy conversion from float32 to uint8. Range [-2.8014118671417236, 3.7762413024902344]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.8014118671417236, 3.754912853240967]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.8014118671417236, 3.9084768295288086]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.8014118671417236, 3.4477851390838623]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.8014118671417236, 3.9340708255767822]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.8014118671417236, 3.6951937675476074]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.8014118671417236, 4.1004319

Lossy conversion from float32 to uint8. Range [-2.8014118671417236, 4.535529613494873]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.8014118671417236, 4.748812675476074]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.8014118671417236, 5.077268600463867]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.8014118671417236, 4.9663615226745605]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.8014118671417236, 4.56965446472168]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.8014118671417236, 5.269223690032959]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.8014118671417236, 6.058371067047

Lossy conversion from float32 to uint8. Range [-2.306645393371582, 3.1989805698394775]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.306645393371582, 4.01984977722168]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.306645393371582, 3.3813960552215576]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.306645393371582, 3.961808443069458]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.306645393371582, 4.243722915649414]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.306645393371582, 4.334930419921875]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.306645393371582, 4.351513862609863]. 

Lossy conversion from float32 to uint8. Range [-2.4402499198913574, 7.396176338195801]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.4402499198913574, 7.016024589538574]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.4402499198913574, 7.36449670791626]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.4402499198913574, 8.291116714477539]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.4402499198913574, 7.728808879852295]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.4402499198913574, 6.493315696716309]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.4402499198913574, 6.3190793991088

Lossy conversion from float32 to uint8. Range [-3.8219411373138428, 11.646082878112793]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-3.8219411373138428, 11.792612075805664]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-3.8219411373138428, 12.351256370544434]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-3.8219411373138428, 12.506943702697754]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-3.8219411373138428, 11.691873550415039]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-3.8219411373138428, 11.728506088256836]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-3.8219411373138428, 11.94830

...

Lossy conversion from float32 to uint8. Range [-4.083411693572998, 6.305342674255371]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-4.083411693572998, 5.386525630950928]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-4.083411693572998, 6.4768548011779785]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-4.083411693572998, 7.922460079193115]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-4.083411693572998, 7.689692974090576]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-4.083411693572998, 8.387993812561035]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-4.083411693572998, 8.620760917663574]. 

Lossy conversion from float32 to uint8. Range [-4.083411693572998, 4.112433433532715]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-4.083411693572998, 5.055751800537109]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-4.083411693572998, 5.202762603759766]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-4.083411693572998, 4.651472568511963]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-4.083411693572998, 4.56571626663208]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-4.083411693572998, 4.247192859649658]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-4.083411693572998, 4.002175331115723]. Co

Lossy conversion from float32 to uint8. Range [-3.7180027961730957, 8.078850746154785]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-3.7180027961730957, 6.593591213226318]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-3.7180027961730957, 5.911832809448242]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-3.7180027961730957, 5.83878755569458]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-3.7180027961730957, 6.386629104614258]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-3.7180027961730957, 7.141432762145996]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-3.7180027961730957, 6.7153339385986

Lossy conversion from float32 to uint8. Range [-5.440743923187256, 5.01370096206665]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-5.440743923187256, 4.510490894317627]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-5.440743923187256, 4.243481636047363]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-5.440743923187256, 4.592647552490234]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-5.440743923187256, 4.654265403747559]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-5.440743923187256, 4.736422061920166]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-5.440743923187256, 4.808309078216553]. Co

Lossy conversion from float32 to uint8. Range [-5.440743923187256, 7.529751300811768]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-5.440743923187256, 7.714603900909424]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-5.440743923187256, 7.848108291625977]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-5.440743923187256, 7.878917217254639]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-5.440743923187256, 7.632447242736816]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-5.440743923187256, 7.673525333404541]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-5.440743923187256, 7.765951633453369]. C

In [19]:
model_name_list = ['ERFAnetZ3_repeat_3_augmentation_none_alpha_1.0_lr_2e-06_epoch_40annealing_down_at_0_beta_0.8_constraint_jacobi_all_gamma_1.0_BRATS2018_t5_s20_l1_u30_WT_epoch31',
                   'ERFAnetZ3_repeat_3_augmentation_none_alpha_1.0_lr_2e-06_epoch_40annealing_down_at_0_beta_0.8_constraint_jacobi_all_gamma_1.0_BRATS2018_t5_s20_l1_u30_WT_epoch32',
                   'ERFAnetZ3_repeat_3_augmentation_none_alpha_1.0_lr_2e-06_epoch_40annealing_down_at_0_beta_0.8_constraint_jacobi_all_gamma_1.0_BRATS2018_t5_s20_l1_u30_WT_epoch33',
                   'ERFAnetZ3_repeat_3_augmentation_none_alpha_1.0_lr_2e-06_epoch_40annealing_down_at_0_beta_0.8_constraint_jacobi_all_gamma_1.0_BRATS2018_t5_s20_l1_u30_WT_epoch34',
                   'ERFAnetZ3_repeat_3_augmentation_none_alpha_1.0_lr_2e-06_epoch_40annealing_down_at_0_beta_0.8_constraint_jacobi_all_gamma_1.0_BRATS2018_t5_s20_l1_u30_WT_epoch35',
                   'ERFAnetZ3_repeat_3_augmentation_none_alpha_1.0_lr_2e-06_epoch_40annealing_down_at_0_beta_0.8_constraint_jacobi_all_gamma_1.0_BRATS2018_t5_s20_l1_u30_WT_epoch36',
                   'ERFAnetZ3_repeat_3_augmentation_none_alpha_1.0_lr_2e-06_epoch_40annealing_down_at_0_beta_0.8_constraint_jacobi_all_gamma_1.0_BRATS2018_t5_s20_l1_u30_WT_epoch37',
                   'ERFAnetZ3_repeat_3_augmentation_none_alpha_1.0_lr_2e-06_epoch_40annealing_down_at_0_beta_0.8_constraint_jacobi_all_gamma_1.0_BRATS2018_t5_s20_l1_u30_WT_epoch38',
                   'ERFAnetZ3_repeat_3_augmentation_none_alpha_1.0_lr_2e-06_epoch_40annealing_down_at_0_beta_0.8_constraint_jacobi_all_gamma_1.0_BRATS2018_t5_s20_l1_u30_WT_epoch39']

model_path = '/home/moucheng/Desktop/IPMI results/BRATS/IPMI2020/ERFAnetZ3_repeat_3_augmentation_none_alpha_1.0_lr_2e-06_epoch_40annealing_down_at_0_beta_0.8_constraint_jacobi_all_gamma_1.0_BRATS2018_t5_s20_l1_u30_WT/trained_models'

test_models(model_name_list, model_path, dataset)

Lossy conversion from float32 to uint8. Range [-2.8014118671417236, 3.7762413024902344]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.8014118671417236, 3.754912853240967]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.8014118671417236, 3.9084768295288086]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.8014118671417236, 3.4477851390838623]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.8014118671417236, 3.9340708255767822]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.8014118671417236, 3.6951937675476074]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.8014118671417236, 4.1004319

Lossy conversion from float32 to uint8. Range [-2.8014118671417236, 4.535529613494873]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.8014118671417236, 4.748812675476074]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.8014118671417236, 5.077268600463867]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.8014118671417236, 4.9663615226745605]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.8014118671417236, 4.56965446472168]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.8014118671417236, 5.269223690032959]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.8014118671417236, 6.058371067047

Lossy conversion from float32 to uint8. Range [-2.306645393371582, 3.1989805698394775]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.306645393371582, 4.01984977722168]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.306645393371582, 3.3813960552215576]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.306645393371582, 3.961808443069458]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.306645393371582, 4.243722915649414]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.306645393371582, 4.334930419921875]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.306645393371582, 4.351513862609863]. 

Lossy conversion from float32 to uint8. Range [-2.4402499198913574, 7.396176338195801]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.4402499198913574, 7.016024589538574]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.4402499198913574, 7.36449670791626]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.4402499198913574, 8.291116714477539]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.4402499198913574, 7.728808879852295]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.4402499198913574, 6.493315696716309]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.4402499198913574, 6.3190793991088

Lossy conversion from float32 to uint8. Range [-3.8219411373138428, 11.646082878112793]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-3.8219411373138428, 11.792612075805664]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-3.8219411373138428, 12.351256370544434]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-3.8219411373138428, 12.506943702697754]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-3.8219411373138428, 11.691873550415039]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-3.8219411373138428, 11.728506088256836]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-3.8219411373138428, 11.94830

...

Lossy conversion from float32 to uint8. Range [-3.286703586578369, 8.448404312133789]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-3.286703586578369, 8.389433860778809]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-3.286703586578369, 8.588459014892578]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-3.286703586578369, 9.119192123413086]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-3.286703586578369, 9.089707374572754]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-3.286703586578369, 8.330463409423828]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-3.286703586578369, 8.942280769348145]. C

Lossy conversion from float32 to uint8. Range [-3.7071266174316406, 8.789691925048828]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-3.7071266174316406, 8.587090492248535]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-3.7071266174316406, 8.90941047668457]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-3.7071266174316406, 8.439743995666504]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-3.7071266174316406, 8.568672180175781]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-3.7071266174316406, 8.642345428466797]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-3.7071266174316406, 8.0529594421386

Lossy conversion from float32 to uint8. Range [-3.3345353603363037, 8.277260780334473]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-3.3345353603363037, 8.487502098083496]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-3.3345353603363037, 8.253002166748047]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-3.3345353603363037, 8.600708961486816]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-3.3345353603363037, 8.859467506408691]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-3.3345353603363037, 9.65191650390625]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-3.3345353603363037, 10.250295639038

Lossy conversion from float32 to uint8. Range [-2.965390205383301, 7.811123847961426]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.965390205383301, 7.965959072113037]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.965390205383301, 7.965959072113037]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.965390205383301, 8.60387897491455]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.965390205383301, 8.994063377380371]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.965390205383301, 8.678199768066406]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float32 to uint8. Range [-2.965390205383301, 8.424270629882812]. Co

KeyboardInterrupt: 